In [18]:
from classes import lfunc_dec, make_keyword_lf,keyword_lookup, SPAM, HAM, ABSTAIN
from textblob import TextBlob
import re
from snorkel.preprocess import preprocessor
from nltk.tokenize import word_tokenize
import os
import glob
import pandas as pd
pd.set_option('display.max_colwidth', -1)
pd.set_option("display.max_rows", None, "display.max_columns", None)
from snorkel.labeling import PandasLFApplier,filter_unlabeled_dataframe
from snorkel.labeling.model import MajorityLabelVoter

In [19]:
all_filenames = [i for i in glob.glob('data/*.csv')]
df = pd.concat([pd.read_csv(f) for f in all_filenames ])
df = df.rename(columns={"CLASS": "label", "CONTENT": "text"})

In [39]:
spams = df[df['label']==SPAM][['text','label']]
hams = df[df['label']==HAM][['text','label']]

In [30]:
spams.shape

(1005, 2)

In [31]:
df.shape

(1956, 5)

In [32]:
spams

text  \
7    SEE SOME MORE SONG OPEN GOOGLE AND TYPE Shakira GuruOfMovie﻿                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       
22   Check out this playlist on YouTube:﻿                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               
31   Support the fight for your 4th amendment right to privacy in your home.  Stop the NSA spying on Americans with the un Patriot Act Renewal. Rand Paul has spent 10.5 hours on the Senate floor in a Protest and Filibuster fighting for our  Constitution that this Nation is founded on. Join the fight at Rand Paul dot com. Spread The Word. We Have Someone That Cares About Our Nation.  Email your Senators, Congress men and women, tell them to support Rand. Tell the news to support Rand too Senator Rand Paul was up until <a href="http://www.youtube.com/watch?v=pRpeEdMmmQ0&amp;t=1m00s">1:00</a> am this passed Saturday morning fighting for our Constitution buy postponing the vote until this week. Our Constitution Matters join Rand in the fight to protect <a href="http://it.ht">it.ht</a> to privacy in your home and business.. Senator Rand Paul was up until <a href="http://www.youtube.com/watch?v=pRpeEdMmmQ0&amp;t=1m00s">1:00</a> am this passed Saturday  morning fighting for our Constitution buy postponing the vote until this week. Our Constitution Matters To All Of US, Help Rand Protect It by joining the fright for it.﻿                                                                              
36   Check out this video on YouTube:﻿                                                                                                                                                                                                                                                                                                                                       

In [40]:
hams

text  \
0    Nice song﻿                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          
1    I love song ﻿                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       
2    I love song ﻿                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       
3    860,000,000 lets make it first female to reach one billion!! Share it and replay it! ﻿                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              
4    shakira is best for worldcup﻿                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       
5    The best world cup song ever!!!!﻿                                                                                                                                                

# Labelling functions

refer to Snorkel tutorial: https://www.snorkel.org/use-cases/01-spam-tutorial

In [33]:
# @lfunc_dec()
# def regex_link(x):
#     return SPAM if re.search(r"http", x.text, flags=re.I) else ABSTAIN

# @lfunc_dec()
# def short_comment(x):
#     """Ham comments are often short, such as 'cool video!'"""
#     return HAM if len(x.text.split()) < 5 else ABSTAIN

import nltk


text = 'subscribe my channel pls'
text = 'Why did they stop their career in music? This music rocks !'
text = "Clinton: US thrived with Clintons in White House"

text = nltk.word_tokenize(text)
result = nltk.pos_tag(text)
# result = [i for i in result if i[0].lower() == 'table']

print(result) # [('table', 'JJ'), ('table', 'VB'), ('table', 'NN')]

[('Clinton', 'NN'), (':', ':'), ('US', 'NNP'), ('thrived', 'VBD'), ('with', 'IN'), ('Clintons', 'NNP'), ('in', 'IN'), ('White', 'NNP'), ('House', 'NNP')]


In [22]:
type(result)

list

In [41]:
@lfunc_dec()
def pos_do_my_stuff(x):
    """VB with PRP$"""
    text = nltk.word_tokenize(x.text)
    posstr = ''.join([t[1] for t in nltk.pos_tag(text)])
    return SPAM if 'VBPRP$' in posstr else ABSTAIN

whynot = make_keyword_lf(keywords=["why not"])

@lfunc_dec()
def nothttp(x):
    """HAM if not https"""
    return HAM if not re.search(r"http", x.text, flags=re.I) else ABSTAIN


In [36]:
def function_check(dataframe, funcs):
    model = MajorityLabelVoter()
    applier = PandasLFApplier(lfs=funcs)
    test_inputs = applier.apply(df=dataframe, progress_bar=False)
    probs_test= model.predict_proba(L=test_inputs)
    df_test_filtered, probs_test_filtered = filter_unlabeled_dataframe(
        X=dataframe, y=probs_test, L=test_inputs
    )
    df_test_filtered = df_test_filtered.reset_index(drop=True)
    train_inputs_filtered = applier.apply(df=df_test_filtered, progress_bar=False)
    df_test_filtered['pred'] = pd.Series(model.predict(L=train_inputs_filtered))
    wrong_preds = df_test_filtered[(df_test_filtered['label']!=df_test_filtered['pred']) & \
                                   (df_test_filtered['pred']!=ABSTAIN)]
    print(f"""
    out of {len(dataframe)} testing data points, {len(df_test_filtered)} actually got at least one signal to \n
    make prediction. Out of all the valid predictions, we have {len(wrong_preds)} wrong predictions, \n
    accuracy = {(len(df_test_filtered)-len(wrong_preds))/len(df_test_filtered)} 
    """)
    return df_test_filtered, wrong_preds

In [42]:
filtered, wrongs = function_check(dataframe=df, funcs=[nothttp])


    out of 1956 testing data points, 1759 actually got at least one signal to 

    make prediction. Out of all the valid predictions, we have 819 wrong predictions, 

    accuracy = 0.5343945423536101 
    


In [43]:
filtered[['text','label','pred']]

text  \
0     Nice song﻿                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   
1     I love song ﻿                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                
2     I love song ﻿                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                
3     860,000,000 lets make it first female to reach one billion!! Share it and replay it! ﻿                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

In [44]:
wrongs

COMMENT_ID  \
7     z12uujnj2sifvzvav04chpypvofvexpoggg           
22    z13zjlpo2nbehxwf322gelhzwmqwgn1mt             
35    z13gv1bxbuytgjl3o23fdr5r3kaadbbm1             
52    z121ireiytz2f1xzz04cc5fznlnchb1jphg           
54    z12hsre40qqswblvg22kvlrhgznxul1xu04           
57    z12zcxyjxof0ihx4w04cf1gojz3zwnty4ts0k         
63    z13azdiwulmkf5kmr22cwbpq1zrntfxby04           
79    z122s1uitnfitv4ru04cet2jquumwz1zsyc0k         
85    z123ydw50qjkfzm5s04cdlzziubxtz0ijfk           
93    z13wd3dwlrifgl3mj22vcdci0yiaubueb             
105   z134y1ki5svvwt43i23wz5kqsxmaettuu             
107   z13chhog1nbldb2xp04cgtkxcx35z1djpf0           
124   z13fzxyw3q3bupy0w22oc3wrmu2qdtmu4             
142   z12jxbfwpnr2u3g1z23sshzxdobre3x0f             
143   z13rv5wieu2fdnogl04cdl0bdmjuunpwcnk0k         
144   z12yhleh5k2lcxtr304chn2gatiwur3xhz40k         
145   z122tvoquqzuirdhu04cfbfznza2jt05juk0k         
146   z13jgncbqw2cwjroj04cfxjisoyrsj2z4kw0k         
147   z13ri55z2su3xp2v123ie1ywjn31zj0sl             
148   z13dhjwwakylwb1ed23vd1mpsmnju5n0o             
149   z13lwva51nepgdxi404ceffbmqnfgje410c           
150   z13axdfy2v21eltyr04cib5jvzz3etij0g0           
151   z12rvnaqcprqe1jmt23fynpy0ziidrrzg04           
152   z13oxjdhkxzqyti1123rvxox2om4fpqqt04           
153   z12ohx343rfzs3nmz22rfnzbkqvqtnxwt04           
154   z13tgdxgmputf1xfk22jjzhqgpi4v3xo104           
155   z13zhngyrsyeffkvf22cjvtofreiub1lp             
156   z13asbvq1n2ttvptn23vd1mpsmnju5n0o             
157   z13szlz5sp2zw3fxc04cc3nbhlmjxnphivg0k         
158   z133vdcgmrijgrhld22zst0i2nfnvdvxa04           
159   z13twxvoxwz1f11pk04cij1b0zi1ifbhdno0k         
160   z12gj5gi4leawfcni225jty5wzvecj53m             
161   z13eupqxoyr2jf4xm04cetijyrjezfxovgw           
162   _2viQ_Qnc6_pJLNSe-ysm1Q4pDNKWrl6EWw0cSIBV14   
163   _2viQ_Qnc6_-PxFkTE_Kx-BN9mjiueYqg5wrx_hMGb4   
164   _2viQ_Qnc6_ZYkMn1fS805Z6oy8ImeO6pSjMLAlwYfM   
165   _2viQ_Qnc6_NsO9XDTWC1TlbTRevVI-QGIqkXxuyl60   
166   _2viQ_Qnc6_J91n3DVA-4R9BjK8WFHtrJvrEn31ogGU   
167   _2viQ_Qnc68YSD3Jr7qwbu0qvY0HeLZysgcn6ievlLI   
168   _2viQ_Qnc6-_qc98D_T8ICCw3meS1f1YJqU9SA-X1t4   
169   _2viQ_Qnc6-FlNdROU4zIseFCr76DMg7l8N-trEo764   
170   _2viQ_Qnc6_1RPym_S70n6Rv617-TI9Z8GVhGlwXs_I   
171   _2viQ_Qnc68YBtosyTVGLy_Fs4YYXoiWd5-wKXnaIw4   
172   _2viQ_Qnc69LaqGJOI7p8VvK_26tIy8R0g_z-_ye79c   
173   _2viQ_Qnc6-fnXF3jNuC5sr8txrOVFd4Uozj9Y4xC-w   
174   _2viQ_Qnc6-awsV_zO5HWBhiYFzj5-4qgeeFv1iJwRU   
175   _2viQ_Qnc69HTQ21lx0wtZ4TFYSpc_gMDApvlQt0q8o   
176   _2viQ_Qnc68YhzlKOdq3h2y3v8TCi0RQSIFzQP8hltY   
177   _2viQ_Qnc6_KD8seCZD8AcEirg_4NEFXuEO1fKw3lmY   
178   _2viQ_Qnc69ShtSmsaBOGFHrTAVCkLAtpOr40oiL5Yg   
179   _2viQ_Qnc69fyi7qH4TDPB7CSJnioSrJi3CoQXBbjCo   
180   _2viQ_Qnc6_kxEjV8Ut57SeEGdqSKmC8VGP1K38Q2qY   
181   _2viQ_Qnc69wKf5GrJmQ5IZqKaEKr-rIjB5OqBC1Y_M   
182   _2viQ_Qnc6-I58GFzl5H7twI_SISp0gQ8DndetxF2i0   
183   _2viQ_Qnc69N53yIJS3ZrRHmdbS1qZLnkXgodzIegJM   
184   _2viQ_Qnc68eqIzELH00rh9umGlUKSRuQvWZAXhr_qM   
185   _2viQ_Qnc69h-dBshypMERLv5by8Rf7I8TSLnP1Lnoo   
186   _2viQ_Qnc6-grcnVFTtwnhvC9tpgVG33p5a0AZHKlLI   
187   _2viQ_Qnc6-q29okw74KTmVXCvhacMZ5NjAiYdAwHww   
188   _2viQ_Qnc69vgWhC2acrKSH-tvjKq1KuKBca1UtB8wk   
189   _2viQ_Qnc69mufWqn8FcFN6u6tahNMkNWgB4-jKb2hs   
190   _2viQ_Qnc6_QZJzAERyAVzhcr3jy2ctVM4zQMfesQWQ   
191   _2viQ_Qnc6_qs30Ph_whafzKoWVyh_xIYpN3-7U_VmA   
192   _2viQ_Qnc69BVRuBYCJ6ik7gdMwTiBRS9DDnTjNs-Gg   
193   _2viQ_Qnc6-nD73Whq8IPs5SpJ3v8OO6PlgvyoopAqQ   
194   _2viQ_Qnc68tZfiBq8O7pExj1MmWcnorsu-kyc0Jz8Q   
195   _2viQ_Qnc6-k1VSPmCd2mrSAAQXChBMxF7oeJGCepUU   
196   _2viQ_Qnc68jroUSzJhg6jrxFj86oxZrAtGB_PWbOm4   
197   _2viQ_Qnc6-dfXGv_qVn1mdoRB9dAfp4ppjUsNu-GDU   
198   _2viQ_Qnc6_eMN0NwT5paySjJPFbN5xI9W8C1Bwoq1U   
199   _2viQ_Qnc68DyUSaxqDmv-6yHPVUpKeYAZhrh2PUMZg   
200   _2viQ_Qnc6-TLlBlT0itl1DbMJQGBx_6ZbscBXA3Nww   
201   _2viQ_Qnc69wrsSgR2azuokmk5-WDQVVI2lCV-WqJGA   
202   _2viQ_Qnc69JZ1f3TJQWKMLhmdP0inDDPwOvzMQiFjE   
208   _2viQ_Qnc6-1fj_YPI5S4X9e9VnvAzoykRbwZGAlYgo   
221   _2viQ

In [45]:
wrongs.index.tolist()

[7,
 22,
 35,
 52,
 54,
 57,
 63,
 79,
 85,
 93,
 105,
 107,
 124,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 157,
 158,
 159,
 160,
 161,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 173,
 174,
 175,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 184,
 185,
 186,
 187,
 188,
 189,
 190,
 191,
 192,
 193,
 194,
 195,
 196,
 197,
 198,
 199,
 200,
 201,
 202,
 208,
 221,
 222,
 223,
 224,
 240,
 241,
 242,
 243,
 244,
 245,
 246,
 247,
 248,
 249,
 250,
 251,
 252,
 254,
 267,
 268,
 269,
 270,
 271,
 280,
 281,
 282,
 283,
 284,
 285,
 286,
 287,
 288,
 289,
 290,
 291,
 292,
 293,
 294,
 295,
 296,
 297,
 298,
 299,
 300,
 301,
 302,
 303,
 304,
 305,
 306,
 307,
 308,
 309,
 310,
 311,
 312,
 313,
 314,
 315,
 316,
 317,
 318,
 319,
 320,
 321,
 322,
 323,
 324,
 325,
 326,
 327,
 328,
 329,
 330,
 331,
 332,
 333,
 334,
 335,
 336,
 337,
 338,
 339,
 343,
 345,
 348,
 349,
 350,
 351,
 352,
 353,
 362,
 363,
 36

In [58]:
test = wrongs[wrongs.index.isin([7, 22, 35])]

In [61]:
test.index.to_list()

[7, 22, 35]

In [50]:
type(test)

pandas.core.series.Series

In [51]:
type(wrongs)

pandas.core.frame.DataFrame

In [62]:
# import pandas as pd

df = pd.DataFrame({'c1': [10, 11, 12], 'c2': [100, 110, 120]})
df = df.reset_index()  # make sure indexes pair with number of rows
for index, row in df.iterrows():
    print(row['c1'], row['c2'])

10 100
11 110
12 120


In [63]:
wrongs.sort_values(['text'], ascending=True)

COMMENT_ID  \
1424  LneaDw26bFuLqTvlvHELy-tdwJHJYoSpv3zRbTj-5SQ   
1423  LneaDw26bFs8EyO6vOIKjYpRt-sa-JxqbsTjjcbiPaQ   
1479  LneaDw26bFt_sZxaSVD4YYGDWlCcEfLjcNyYrRWcSrg   
1085  z13sfvhiwxmqz3xad04cddehoyr5g1i5c0s           
223   _2viQ_Qnc6_xOpLcxFFeUEgEYvQjttGcFYeMZ2lK4yY   
222   _2viQ_Qnc6-kUg8jc2n9-Cudm5lEsM-cSzIjF182TJo   
898   z13eglu51lmgxbhj304cfh2ifo3phfqwa3k           
544   z13oc52ihn22tfz3n231vv4bvxrujn0f0             
1095  z12hzb1hzxbjh310c234ddqgoluidjufb             
1747  LneaDw26bFsFwQBcbaeKWWcSsBB7EA1zRf2nBgT9NyY   
395   z13csdop4venytrru04cf11q1wmbdvkrfpo0k         
1373  LneaDw26bFshLT1-9YrPxWqbLzAdCIz2qsKDoIM2SDY   
1570  LneaDw26bFuFItWTKmffBRPA4v3HwunSq-ceF3kwQZ4   
224   _2viQ_Qnc6_7GI-VeVlj8gEzvkgATIX3jK-7J1kwWEY   
373   z13xit5agm2zyh4f523rst2gowmbx5bml             
1705  LneaDw26bFv9y-1cf9oawnpCocMFtK6HXTRuoffJR2k   
175   _2viQ_Qnc69HTQ21lx0wtZ4TFYSpc_gMDApvlQt0q8o   
1420  LneaDw26bFtwg5A1ijrcWVqI_5EptEDoyiygIJl5Xp4   
169   _2viQ_Qnc6-FlNdROU4zIseFCr76DMg7l8N-trEo764   
268   _2viQ_Qnc68RkAwC42s4YBDdCJYELSb6UiuZri58Kn0   
335   _2viQ_Qnc6_AXZ4E5CeA3LHE36RAijd3QKgUI-YvjWI   
316   _2viQ_Qnc6_Hcona9vbTbZqnb5SyyHKi7PxVC-KkfTY   
349   _2viQ_Qnc6_HU65mTzCmXnjA-WLt7XqxqPj7EwAtlO0   
1651  LneaDw26bFsPpgYyHcGAJk2dyALknpZ1ITQKBmY32HI   
352   _2viQ_Qnc69MEEHHJxZ427KX8MlljJPnUC2YBbvbWwY   
351   _2viQ_Qnc6_fgKR1W7-k1lbVURi8hVbMlQAMSOCSnyk   
353   _2viQ_Qnc6_RKHVetk9kLzx8ZC62_J7y73FWFSBTe8Q   
1578  LneaDw26bFuGts11KE-vf8DxNybKxvOCLkkkExJk2pk   
1317  z12rwfnyyrbsefonb232i5ehdxzkjzjs2             
1162  z132zl1rupqcylbep23jgfig3um3ct5vv             
400   z12ktfsarrv0wdj3p22ifbxz3zn2fthhw04           
247   _2viQ_Qnc69uhVbXr8SjkhLHu7T1HOxqrEF1f6h8vUA   
1695  LneaDw26bFuFgDF5yE6Udiuv2lqie4iaimFPdN7rvYk   
208   _2viQ_Qnc6-1fj_YPI5S4X9e9VnvAzoykRbwZGAlYgo   
1756  LneaDw26bFuvs-8oWkLpAFa6g3QHpWD8k7sbbMP3Bg8   
1012  z13rs3fimnydzjdu423qudibdzm0sbyjh04           
286   _2viQ_Qnc69AVbPU2gXuoLiAOr6muFqsr7sm17CjhX4   
1240  z13xuxwywsewv3dvu23jgfig3um3ct5vv             
170   _2viQ_Qnc6_1RPym_S70n6Rv617-TI9Z8GVhGlwXs_I   
1433  LneaDw26bFvxF3dtP-JPmr1RRfbcmnhR8cXBDGWcO2M   
868   z12ejj24lzmnwd5ex231czmjbmestruas04           
1031  z12ghvgo3xjyjvouf23tstj5bna5jei0              
1328  z13nsd141x24yjh2m224xvlhisrqet4pj04           
1251  z135jfhquofkjjxam04cdraphzuxxry4iso0k         
1673  LneaDw26bFvxJlVsbYMPkvV3LnT9JOJjEg5OsTN9pMo   
439   z13zfpqpvpyvwfymk232ux4odsr1s5wm0             
1204  z13wt1vrismyzpiij04cj5vz4nzlyj4yfzo0k         
1324  z12gxdortqzwhhqas04cfjrwituzghb5tvk0k         
926   z134vn15sxiwyfzhv04ch3no3zj2sdsqqw40k         
1364  z12vv12yzxuzhnaw104cg3hyboiwyvc4ea0           
185   _2viQ_Qnc69h-dBshypMERLv5by8Rf7I8TSLnP1Lnoo   
221   _2viQ_Qnc6_rAWi6BK2OqTQ_Ob0X8DkXenO0qL0qWm0   
486   z12scr5ixnexwh2xa04civ3o3k25dr3wkfw           
475   z13osluqrpefv1hd323idhejzxanc3ai004           
240   _2viQ_Qnc69D1Jxs1IlkkF0Xzce0uBoJN_OzDHnfmV0   
1387  LneaDw26bFsrleSoC9hVAdk8QmJCwfmQ1BuBDhQBQ6E   
381   LZQPQhLyRh9EXArr4ZnVcDonSbvSMHKYOT24e_qR6fE   
1714  LneaDw26bFsYJ3OzV2q22gR6I5MvSlIF8ve1WpZHnqg   
1528  LneaDw26bFttCkyddOJEPH8MvdMEkuYK_CTH-fLEm8E   
1618  LneaDw26bFspwHUoVH2c1_LONmdspcoJ2HoRzSx0cV8   
1701  LneaDw26bFsw47hS3RAHCBj_uNPFQNZVbUVyx5Rh9zk   
298   _2viQ_Qnc6_yLBNpqStGB5UF3nD3razd5EYm60rdOKs   
1357  z13ktfeorojjx3dbd04cdzngspmlzj5qghs           
1649  LneaDw26bFtdk45hGIs0TDD3NHx1srFG99yWWbEIXG0   
1558  LneaDw26bFuXMGzeve-9_Piipp0wpaS_5AJyXS2fqJw   
1667  LneaDw26bFvq7Rq_343ImPD-uDHf2clFCLMRkYqXPX4   
318   _2viQ_Qnc6-h3o48aXYmI_xInBcH9saCmEK627IQm68   
1602  LneaDw26bFvSkELgnp-ZdS5ZiYbn_tFmogawXBUucN4   
613   z12kw53jipujdzqex22qt5vxtoyde3cwg04           
1591  LneaDw26bFtHPL0j2tW4vknwh8imHXGX4vzYDmr2nhc   
536   z12hidxilpv4uduvf23jdjp4nleeulehc04           
940   z13qfdrbsxfawpbzz04cclnxskurjhjwgas           
161   z13eupqxoyr2jf4xm04cetijyrjezfxovgw           
1114  z12zu5v4qlruc11zc04cg5rrnzjehpzwv3g           
196   _2viQ_Qnc68jroUSzJhg6jrxFj86oxZrAtGB_PWbOm4   
1554  LneaD